## Write old papers database

In [31]:
import django
import os
import pandas as pd
import numpy as np
from old_database.modules_webpage import read_publications, read_addresses

os.environ.setdefault("DJANGO_SETTINGS_MODULE", "nanotud.settings")
from django.core.wsgi import get_wsgi_application
application = get_wsgi_application()
from research.models import Publication
# needed when run inter jupyter enviornment:
os.environ["DJANGO_ALLOW_ASYNC_UNSAFE"] = "true"
django.setup()


import html
import namedentities as ne
def html_coding(string):
    """Converts string to HTML entities.
    """
    string = ne.named_entities(html.escape(string))
    return string


path_papers = 'old_database/database.papers'
df_papers = read_publications(path_papers)

In [23]:
df_papers

In [32]:
# take only publications with DOI
df_papers = df_papers[~df_papers['DOI'].isnull()]

In [5]:
len(df_papers['DOI'].unique())

476

In [27]:
df_papers[df_papers.duplicated(subset='DOI', keep=False)][['title','DOI','year','cvselected','type']]

Empty DataFrame
Columns: [title, DOI, year, cvselected, type]
Index: []

In [28]:
df_papers['type'].unique()

array(['regular', 'review', 'letter', 'book'], dtype=object)

In [ ]:
for col in df_papers.isna().sum().sort_values().index.values:
    try:
        print (col,'\t\tNaN_count:',df_papers[col].isnull().value_counts()[1])
    except:
        print (col,'ALL')

In [ ]:
df_papers[df_papers['reference'].isnull()][['title','DOI','year']]

In [ ]:
test ='<i>J. Phys.: Cond. Matter</i> <b>24</b>, 394003 (2012)'
test.split('</b>')[1]

In [33]:
# only publications with reference
df_papers = df_papers[~df_papers['reference'].isnull()]
# df_papers = df_papers[~(df_papers['type']=='inbook')]

In [35]:
for index, row in df_papers.iterrows():
    ref=row['reference']
    try:
        journal_short = ref.split('<i>')[1].strip().split('</i>')[0].strip()
    except:
        print (ref)
    try:
        volume = ref.split('<b>')[1].split('</b>')[0]
    except:
        volume= ''
    try:
        page = ref.split('</b>')[1].split('(')[0].strip(',').strip()
    except:
        page=0
    if type(row['pubdate']) == float:
        pubdate = f"{row['year']}-12-01"
    else:
        pubdate = row['pubdate'].replace('.','-')
    
    try:
        if row['cvselected'] == 'yes': 
            cvselected = 'True'
            print (ref)
        else:
            cvselected = 'False'
    except:
        cvselected = 'False'
        
    title = html.unescape(row['title'])
    author_list = html.unescape(row['authors'])
    try:
        abstract = html.unescape(row['abstract'])
    except:
        abstract=''

    new_publication = Publication(doi=row['DOI'],
                          page=page,
                          pub_type=row['type'],
                          journal_short=journal_short,
                          cvselected=cvselected,
                          title=title,
                          author_list=author_list,
                          abstract=abstract,
                          volume=volume,
                          year=int(row['year']),
                          pub_date=pubdate,
                        )
    new_publication.save()

<i>Nature Electronics</i> <b>3</b>, 398-408 (2020)
<i>Nature Communications</i> <b>9</b>, 4051 (2018)
<i>Nature Materials</i> <b>17</b> 439 (2018)
<i>Nano Letters</i> <b>16</b>, 4991 (2016)
<i>Nature Scientific Reports</i> <b>3</b>, 1228 (2013)
<i>Advanced Materials</i> <b>23</b>, 4471 (2011)
<i>Physical Review Letters</i> <b>102</b>, 208102 (2009)
<i>Nature Materials</i> <b>7</b>, 68 (2008)
<i>Nature Nanotechnology</i> <b>2</b>, 176 (2007)
<i>Physical Review Letters</i> <b>96</b>, 076802 (2006)
<i>Lecture Notes in Physics</i> <b>680</b> (Springer, Berlin and Heidelberg, 2005)
